# Empenhos da Cultura Cearense
- Trabalho de Extração de dados
- Disciplina: Introdução à Ciência de Dados
- Estudante: Renato Freitas

## Gastos Públicos no Setor Cultural


Onde | R\$ | 2011 | R\$ | 2018
---|--|---------|--|----------
Gastos nas três esferas | R\$ 7.1 bilhões || R\$ 9.1 bilhões|
Federal | R\$ 1.360.528 | 19.2\% | R\$ 1.925.133 | 21.1\%
Estadual | R\$ 2.270.552 | 32.0\% | R\$ 2.504.970 | 27.5\%
Municipal | R\$ 3.462.388 | 48.8\% | R\$ 4.690.086 | 51.4\%
Despesas dos municípios cearenses | - |3.8\%| - |4.3\%


Fonte: IBGE, Sistema de Informações e Indicadores Culturais. https://biblioteca.ibge.gov.br/visualizacao/livros/liv101687.pdf

## Objetivo
Gerar um dataset de empenhos da cultura cearense dos cinco últimos anos.

## Fonte de Dados
Portal de Sitemas e Consultas Municípios - TCE. https://municipios.tce.ce.gov.br/

<img src="tcm.png" />

##  Como obter os dados.
Módulo Dados Abertos - via API.

Para obter os empenhos é preciso conhecer o código do município, do órgão e informar ano pretendido.
 - PASSO 1. OBTER OS CÓDIGOS DOS MUNICÍPIOS
 - PASSO 2. OBTER OS CÓDIGOS DOS ORGÃO (SECRETARIA DE CULTURA, POR EXEMPLO)
 - PASSO 3. OBTER OS EMPENHOS

### PASSO 1. OBTER OS CÓDIGOS DOS MUNICÍPIOS

In [1]:
# Bibliotecas
import requests
from bs4 import BeautifulSoup
from datetime import date
import csv
import pandas as pd
import json
import logging
import time

In [2]:
# Armazena todos os municípios do Ceará. 
municipios = []

In [3]:
# API do Tribunal de Contas do Estado do Ceará
api_tce = "https://api.tce.ce.gov.br/index.php/sim/1_0/"

In [4]:
# Rota dos municipios no TCE
rota_municipios = "{}municipios.json?".format(api_tce)

response = requests.get(rota_municipios)
municipios = response.json()["rsp"]["_content"]

print("Municípios: {}".format(len(municipios)))

Municípios: 184


### PASSO 2. OBTER OS CÓDIGOS DOS ORGÃOS 
(SECRETARIA DE CULTURA, POR EXEMPLO)

In [5]:
#https://api.tce.ce.gov.br/index.php/sim/1_0/unidades_orcamentarias?codigo_municipio=002&exercicio_orcamento=201800

ano_atual = date.today().year
ini_orgaos = time.time()

# Obter todos os orgão nos últimos 4 anos, ou seja, da última gestão.
for municipio in municipios:
    orgao = {}
    orgaos_cultura = []
    for ano in range(ano_atual - 4, ano_atual):
        cod_mun_tce = municipio["codigo_municipio"]
        rota_orgaos = "{}unidades_orcamentarias.json?codigo_municipio={}&exercicio_orcamento={}00".format(api_tce, cod_mun_tce, ano)
    
        response = requests.get(rota_orgaos)
        conteudo = response.text.replace("\\", "\\\\")
        orgaos = json.loads(conteudo)["rsp"]["_content"]
        
        for key in orgaos:
            NOME_ORG = key["nome_unidade"].upper()
            if NOME_ORG.find("CULTURA") != -1 and NOME_ORG.find("AGRICULTURA") == -1 and NOME_ORG.find("AQUICULTURA") == -1:
                orgaos_cultura.append([key["codigo_orgao"], key["nome_unidade"], str(ano)])
                
        municipio["orgaos"] = orgaos_cultura
fim_orgaos = time.time()  
print("Tempo: {}seg.".format(fim_orgaos - ini_orgaos))
municipios

Tempo: 200.02530026435852seg.


[{'codigo_municipio': '002',
  'nome_municipio': 'ABAIARA',
  'geoibgeId': '2300101',
  'orgaos': [['06', 'SECRETARIA DE CULTURA', '2017'],
   ['06', 'Secretaria de Cultura', '2018'],
   ['06', 'Secretaria de Cultura', '2019'],
   ['06', 'Secretaria de Cultura', '2020']]},
 {'codigo_municipio': '003',
  'nome_municipio': 'ACARAPE',
  'geoibgeId': '2300150',
  'orgaos': [['08', 'Secretaria de Cultura, Esporte e Lazer', '2017'],
   ['08', 'Secretaria de Cultura, Esporte e Lazer', '2018'],
   ['08', 'Secretaria de Cultura, Esporte e Lazer', '2019'],
   ['08', 'Secretaria de Cultura, Esporte e Lazer', '2020']]},
 {'codigo_municipio': '004',
  'nome_municipio': 'ACARAU',
  'geoibgeId': '2300200',
  'orgaos': [['09', 'SECRETARIA DE CULTURA E TURISMO', '2017'],
   ['09', 'SECRETARIA DE CULTURA E TURISMO', '2018'],
   ['08', 'Secretaria de Turismo e Cultura', '2019'],
   ['08', 'Secretaria de Turismo e Cultura', '2020']]},
 {'codigo_municipio': '005',
  'nome_municipio': 'ACOPIARA',
  'geoibge

### PASSO 3. OBTER OS EMPENHOS

In [6]:
#https://api.tce.ce.gov.br/index.php/sim/1_0/notas_empenhos?codigo_municipio=014&codigo_orgao=06&data_referencia_empenho=201101
def obtemRotaEmpenhos(cod_mun_ce, cod_org_tce, ano): 
    """Recebe o código do municipio, o código do orgão e o ano"""
    
    return """{}notas_empenhos.json?codigo_municipio={}&codigo_orgao={}&data_referencia_empenho={}01""".format(api_tce, cod_mun_ce, cod_org_tce, ano)

In [8]:
empenhos = []
ini_empenhos = time.time()
for municipio in municipios:
    print(municipio["nome_municipio"], end=' ')
    for orgao in municipio["orgaos"]:
        url = obtemRotaEmpenhos(municipio["codigo_municipio"], orgao[0], orgao[2])
        response = requests.get(url)
        conteudo = response.text.replace("\\", "\\\\")        
        empenhos.extend(json.loads(conteudo, strict=False)["rsp"]["_content"])
        
fim_empenhos = time.time()     
print("Tempo: {}".format(fim_empenhos - ini_empenhos))
len(empenhos)

ABAIARA ACARAPE ACARAU ACOPIARA AIUABA ALCANTARAS ALTANEIRA ALTO SANTO AMONTADA ANTONINA DO NORTE APUIARES AQUIRAZ ARACATI ARACOIABA ARARIPE ARATUBA ARNEIROZ ASSARE AURORA BAIXIO BANABUIU BARBALHA BARREIRA BARRO BARROQUINHA BATURITE BEBERIBE BELA CRUZ BOA VIAGEM BREJO SANTO CAMOCIM CAMPOS SALES CANINDE CAPISTRANO CARIDADE CARIRE CARIRIACU CARIUS CARNAUBAL CASCAVEL CATARINA CAUCAIA CEDRO CHAVAL CHOROZINHO COREAU CRATEUS CRATO CROATA CRUZ DEPUTADO IRAPUAN PINHEIRO ERERE EUSEBIO FARIAS BRITO FORQUILHA FORTALEZA FRECHEIRINHA GENERAL SAMPAIO GRACA GRANJA GRANJEIRO GROAIRAS GUAIUBA GUARACIABA DO NORTE GUARAMIRANGA HIDROLANDIA HORIZONTE IBARETAMA IBIAPINA IBICUITINGA ICAPUI ICO IGUATU INDEPENDENCIA IPAPORANGA IPAUMIRIM IPU IPUEIRAS IRACEMA IRAUCUBA ITAICABA ITAPAJE ITAPIPOCA ITAPIUNA ITAREMA ITATIRA JAGUARETAMA JAGUARIBARA JAGUARIBE JAGUARUANA JARDIM JATI JUAZEIRO DO NORTE JUCAS LAVRAS DA MANGABEIRA LIMOEIRO DO NORTE MADALENA MARACANAU MARANGUAPE MARCO MARTINOPOLE MASSAPE MAURITI MERUOCA MILA

20745

In [9]:
empenhos

[{'codigo_municipio': '002',
  'exercicio_orcamento': '201700',
  'codigo_orgao': '06',
  'codigo_unidade': '01  ',
  'data_emissao_empenho': '2017-01-02 00:00:00',
  'numero_empenho': '02010005',
  'data_referencia_empenho': '201701',
  'codigo_funcao': '13',
  'codigo_subfuncao': '122',
  'codigo_programa': '0030',
  'codigo_projeto_atividade': '2',
  'numero_projeto_atividade': '023',
  'numero_subprojeto_atividade': '0000',
  'codigo_elemento_despesa': '31901100',
  'modalidade_empenho': 'E',
  'descricao_empenho': 'Valor que se empenha p/ fazer face as despesas com DISPENDIO COM O PESSOAL LOTADOS JUNTO A ESTA SECRETARIA DE CULTURA NO PRESENTE EXERCICIO FINANCEIRO DE 2017, NESTE MUNICIPIO DE ABAIARA.',
  'valor_anterior_saldo_dotacao': '59550.8000',
  'valor_empenhado': '59550.0000',
  'valor_atual_saldo_dotacao': '0.8000',
  'tipo_processo_licitatorio': 'F',
  'numero_documento_negociante': '66666666666',
  'estado_empenho': 'AP',
  'numero_nota_anulacao': ' ',
  'data_emissao_emp

## Agregar valor aos empenhos 
Obter situação, data da situação, atiividade primária e código da atividade primária da empresa.

Investigando como o Projeto Serenato de Amor faz consultas à CNPJs, descobriu-se a API de ReceitaWs.

Site: https://serenata.ai/

Site|Github
:--:|:--:
<img src="serenata.png" width="600"/>|<img src="git.png" />

Site: https://receitaws.com.br/

ReceitaWS|Planos
:--:|:--:
<img src="receita.png" width=600>|<img src="receita-planos.png">

In [10]:
def cnpjNaoExiste(cnpj, data):
    return {'cnpj': cnpj, 'ultima_atualizacao': data, 'status': 'ERROR', 'message': 'CNPJ rejeitado pela Receita Federal', 'billing': {'free': True, 'database': True}}

In [11]:
# Obter situacao dos CNPJS
# Fonte: https://github.com/okfn-brasil/serenata-de-amor/blob/main/research/src/fetch_cnpj_info.py
logger = logging.getLogger('fetch_cnpj')

def fetch_cnpj_info(cnpj, timeout=60):
    url = 'http://receitaws.com.br/v1/cnpj/%s' % cnpj
    
    try:
        response = requests.get(url,timeout=timeout)
        if response.status_code == 200:
            return response.json()
        elif response.status_code == 429:
            logger.debug('Sleeping 60 seconds to try again.')
            time.sleep(60)
            response2 = requests.get(url,timeout=timeout)
#             print("sleep 60 secs: ",response2.status_code)
            return response2.json()
        else:
            return cnpjNaoExiste(cnpj, date.today())
            print(response.text)
    except requests.exceptions.Timeout as e:
        logger.debug(e)
    except requests.exceptions.ConnectionError as e:
        logger.debug(e)

In [12]:
# Testando a função fetch_cnpj_info()
ex3_situacao = fetch_cnpj_info("00000000053201")
print("ex3: ", ex3_situacao)

ex3:  {'atividade_principal': [{'text': 'Bancos múltiplos, com carteira comercial', 'code': '64.22-1-00'}], 'data_situacao': '03/11/2005', 'tipo': 'FILIAL', 'nome': 'BANCO DO BRASIL SA', 'efr': 'UNIÃO', 'uf': 'CE', 'telefone': '(88) 3643-9900', 'email': 'age0532@bb.com.br', 'atividades_secundarias': [{'text': 'Outras atividades de serviços financeiros não especificadas anteriormente', 'code': '64.99-9-99'}], 'situacao': 'ATIVA', 'bairro': 'CENTRO', 'logradouro': 'AV DOS CONSTITUINTES', 'numero': '68', 'cep': '62.350-000', 'municipio': 'UBAJARA', 'porte': 'DEMAIS', 'abertura': '01/08/1966', 'natureza_juridica': '203-8 - Sociedade de Economia Mista', 'fantasia': 'UBAJARA (CE)', 'cnpj': '00.000.000/0532-01', 'ultima_atualizacao': '2021-03-02T02:00:45.768Z', 'status': 'OK', 'complemento': '', 'motivo_situacao': '', 'situacao_especial': '', 'data_situacao_especial': '', 'capital_social': '0.00', 'qsa': [], 'extra': {}, 'billing': {'free': True, 'database': True}}


In [13]:
# Adicionar situacao da Empresa ao dataset
favorecidos = {}
inicio = time.time()
count = 1
#8161 
for empenho in empenhos:
    print(count, end=' ') if count%100==0 else None
    count += 1
    cpfCnpj = str(empenho["numero_documento_negociante"]).strip()
    
    empenho["situacao_favorecido"] = ""
    empenho["data_situacao"] = ""
    empenho["atividade_principal_texto"] = ""
    empenho["atividade_principal_codigo"] = ""
    
    if len(cpfCnpj) == 14:
        
        cnpjJaConsultado = favorecidos.get(cpfCnpj)
        
        if cnpjJaConsultado != None:
            print("CNPJ {} JÁ consultado!".format(cpfCnpj)) if count%100==0 else None
            empenho["situacao_favorecido"] = cnpjJaConsultado["situacao"]
            empenho["data_situacao"] = cnpjJaConsultado["data_situacao"]
            empenho["atividade_principal_texto"] = cnpjJaConsultado["atividade_principal"][0]["text"]
            empenho["atividade_principal_codigo"] = cnpjJaConsultado["atividade_principal"][0]["code"]
        else:
#             print("CNPJ {} ainda NÃO consultado".format(cpfCnpj))
            favorecido = fetch_cnpj_info(cpfCnpj)
            if favorecido != None and favorecido["status"].upper() == "OK":
                empenho["situacao_favorecido"] = favorecido["situacao"]
                empenho["data_situacao"] = favorecido["data_situacao"]
                empenho["atividade_principal_texto"] = favorecido["atividade_principal"][0]["text"]
                empenho["atividade_principal_codigo"] = favorecido["atividade_principal"][0]["code"]
                favorecidos[cpfCnpj] = favorecido
            else:
                empenho["situacao_favorecido"] = favorecido["message"]
                empenho["data_situacao"] = favorecido["ultima_atualizacao"]
                empenho["atividade_principal_texto"] = ""
                empenho["atividade_principal_codigo"] = ""
fim = time.time()
print("\nCNPJ's distintos: {}".format(len(favorecidos)))
print("Tempo para Consultar os CNPJs: {}".format(fim - inicio))

100 200 300 400 CNPJ 04044328000160 JÁ consultado!
500 CNPJ 24564509000125 JÁ consultado!
600 CNPJ 26951783000182 JÁ consultado!
700 CNPJ 27260408000159 JÁ consultado!
800 CNPJ 07047251000170 JÁ consultado!
900 1000 1100 CNPJ 29979036005290 JÁ consultado!
1200 1300 CNPJ 07654272000154 JÁ consultado!
1400 CNPJ 07779242000174 JÁ consultado!
1500 CNPJ 07047251000170 JÁ consultado!
1600 1700 1800 CNPJ 07047251000170 JÁ consultado!
1900 2000 2100 2200 CNPJ 00000000000191 JÁ consultado!
2300 CNPJ 07047251000170 JÁ consultado!
2400 2500 2600 2700 2800 2900 3000 3100 CNPJ 13485158000140 JÁ consultado!
3200 CNPJ 23581150000131 JÁ consultado!
3300 3400 3500 3600 3700 3800 3900 4000 4100 4200 CNPJ 41644220000135 JÁ consultado!
4300 CNPJ 07135601000746 JÁ consultado!
4400 CNPJ 03445908000105 JÁ consultado!
4500 4600 CNPJ 07047251000170 JÁ consultado!
4700 4800 CNPJ 07040108000157 JÁ consultado!
4900 5000 CNPJ 15410425000146 JÁ consultado!
5100 CNPJ 00360305000104 JÁ consultado!
5200 5300 5400 5500

In [14]:
len(empenhos)

20745

### Criar CSV

In [15]:
cabecalhos = empenhos[0].keys()
cabecalhos

dict_keys(['codigo_municipio', 'exercicio_orcamento', 'codigo_orgao', 'codigo_unidade', 'data_emissao_empenho', 'numero_empenho', 'data_referencia_empenho', 'codigo_funcao', 'codigo_subfuncao', 'codigo_programa', 'codigo_projeto_atividade', 'numero_projeto_atividade', 'numero_subprojeto_atividade', 'codigo_elemento_despesa', 'modalidade_empenho', 'descricao_empenho', 'valor_anterior_saldo_dotacao', 'valor_empenhado', 'valor_atual_saldo_dotacao', 'tipo_processo_licitatorio', 'numero_documento_negociante', 'estado_empenho', 'numero_nota_anulacao', 'data_emissao_empenho_substituto', 'numero_empenho_substituto', 'cd_cpf_gestor', 'cpf_gestor_contrato', 'data_contrato', 'numero_contrato', 'data_realizacao_licitacao', 'numero_licitacao', 'codigo_tipo_negociante', 'nome_negociante', 'endereco_negociante', 'fone_negociante', 'cep_negociante', 'nome_municipio_negociante', 'codigo_uf', 'tipo_fonte', 'codigo_fonte', 'situacao_favorecido', 'data_situacao', 'atividade_principal_texto', 'atividade_pr

In [21]:
empenhos_copy = empenhos
len(empenhos_copy)

20745

In [22]:
t_init = time.time()
for e in empenhos_copy:
    for m in municipios:
        if (e['codigo_municipio'] == m['codigo_municipio']):
            e['nome_municipio'] = m['nome_municipio']
            break;            
            
t_end = time.time()
print('\n\nTime: {}'.format(t_end - t_init))
    



Time: 0.28121447563171387


In [23]:
empenhos_copy

[{'codigo_municipio': '002',
  'exercicio_orcamento': '201700',
  'codigo_orgao': '06',
  'codigo_unidade': '01  ',
  'data_emissao_empenho': '2017-01-02 00:00:00',
  'numero_empenho': '02010005',
  'data_referencia_empenho': '201701',
  'codigo_funcao': '13',
  'codigo_subfuncao': '122',
  'codigo_programa': '0030',
  'codigo_projeto_atividade': '2',
  'numero_projeto_atividade': '023',
  'numero_subprojeto_atividade': '0000',
  'codigo_elemento_despesa': '31901100',
  'modalidade_empenho': 'E',
  'descricao_empenho': 'Valor que se empenha p/ fazer face as despesas com DISPENDIO COM O PESSOAL LOTADOS JUNTO A ESTA SECRETARIA DE CULTURA NO PRESENTE EXERCICIO FINANCEIRO DE 2017, NESTE MUNICIPIO DE ABAIARA.',
  'valor_anterior_saldo_dotacao': '59550.8000',
  'valor_empenhado': '59550.0000',
  'valor_atual_saldo_dotacao': '0.8000',
  'tipo_processo_licitatorio': 'F',
  'numero_documento_negociante': '66666666666',
  'estado_empenho': 'AP',
  'numero_nota_anulacao': ' ',
  'data_emissao_emp

In [24]:
cabecalhos = empenhos_copy[0].keys()
cabecalhos

dict_keys(['codigo_municipio', 'exercicio_orcamento', 'codigo_orgao', 'codigo_unidade', 'data_emissao_empenho', 'numero_empenho', 'data_referencia_empenho', 'codigo_funcao', 'codigo_subfuncao', 'codigo_programa', 'codigo_projeto_atividade', 'numero_projeto_atividade', 'numero_subprojeto_atividade', 'codigo_elemento_despesa', 'modalidade_empenho', 'descricao_empenho', 'valor_anterior_saldo_dotacao', 'valor_empenhado', 'valor_atual_saldo_dotacao', 'tipo_processo_licitatorio', 'numero_documento_negociante', 'estado_empenho', 'numero_nota_anulacao', 'data_emissao_empenho_substituto', 'numero_empenho_substituto', 'cd_cpf_gestor', 'cpf_gestor_contrato', 'data_contrato', 'numero_contrato', 'data_realizacao_licitacao', 'numero_licitacao', 'codigo_tipo_negociante', 'nome_negociante', 'endereco_negociante', 'fone_negociante', 'cep_negociante', 'nome_municipio_negociante', 'codigo_uf', 'tipo_fonte', 'codigo_fonte', 'situacao_favorecido', 'data_situacao', 'atividade_principal_texto', 'atividade_pr

In [25]:
# Cria o arquivo.
#1 - 8161
arquivo_csv = open('empenhos_m.csv', 'w', newline='', encoding='utf-8')

# Cria o objeto de gravação
escrever = csv.writer(arquivo_csv, delimiter=',')

# Grava os cabecalhos
escrever.writerow(cabecalhos)

for linha in empenhos_copy:
    escrever.writerow(linha.values())

# Fecha o arquivo.
arquivo_csv.close()

In [27]:
# df = pd.read_csv("empenhos_ce.csv")
# df2 = pd.read_csv("empenhos_ce2.csv")
# df3 = pd.read_csv("empenhos_ce3.csv")
df = pd.read_csv('empenhos_m.csv')

In [28]:
df

codigo_municipio  exercicio_orcamento  codigo_orgao  codigo_unidade  \
0                     2               201700             6               1   
1                     2               201800             6               1   
2                     2               201800             6               1   
3                     2               201800             6               1   
4                     2               201900             6               1   
...                 ...                  ...           ...             ...   
20740               185               202000            16               1   
20741               185               202000            16               1   
20742               185               202000            16               1   
20743               185               202000            16               1   
20744               185               202000            16               1   

      data_emissao_empenho numero_empenho  data_referencia_empenho  \
0      2017-01-02 00:00:00       02010005                   201701   
1      2018-01-03 00:00:00       03010004                   201801   
2      2018-01-02 00:00:00       02010131                   201801   
3      2018-01-02 00:00:00       02010019                   201801   
4      2019-01-02 00:00:00       02010112                   201901   
...                    ...            ...                      ...   
20740  2020-01-02 00:00:00       02010289                   202001   
20741  2020-01-06 00:00:00       06010005                   202001   
20742  2020-01-13 00:00:00       13010040                   202001   
20743  2020-01-13 00:00:00       13010041                   202001   
20744  2020-01-20 00:00:00       20010079                   202001   

       codigo_funcao  codigo_subfuncao  codigo_programa  ...  cep_negociante  \
0                 13               122               30  ...        63240000   
1                 13               122               30  ...        63190000   
2                 13               122               30  ...        63041155   
3                 13               122               30  ...        63240000   
4                 13               122               30  ...        63240000   
...              ...               ...              ...  ...             ...   
20740             13               392               28  ...        70002900   
20741             13               392               28  ...        62030120   
20742             13               392               28  ...        62580970   
20743             13               392               28  ...        60750022   
20744             13               392               28  ...        60832402   

       nome_municipio_negociante  codigo_uf  tipo_fonte codigo_fonte  \
0                        Abaiara         CE           1            1   
1              Santana do Cariri         CE           1            1   
2              Juazeiro do Norte         CE           1            1   
3                        Abaiara         CE           1            1   
4                        ABAIARA         CE           1      1000000   
...                          ...        ...         ...          ...   
20740                   Brasilia         DF           1      1000000   
20741                     Sobral         CE           1      1000000   
20742                     Acarau         CE           1      1000000   
20743                  Fortaleza         CE           1      1000000   
20744                  Fortaleza         CE           1      1000000   

      situacao_favorecido  data_situacao  \
0                     NaN            NaN   
1                     NaN            NaN   
2                   ATIVA     13/11/2006   
3                     NaN            NaN   
4                   ATIVA     03/11/2005   
...                   ...            ...   
20740               ATIVA     03/11/2005   
20741               ATIVA     03/11/2005   
20742  